## Zadanie nr 2

### Import pakietów i danych

In [3]:
import dalex as dx
import pandas as pd
import numpy as np
from sklearn.datasets import fetch_openml

In [4]:
df = fetch_openml(data_id = 43398)
df = df.data
X = df.iloc[:,0:13]
y = df.iloc[:,13]

/usr/local/lib/python3.10/dist-packages/sklearn/datasets/_openml.py:968: FutureWarning: The default value of `parser` will change from `'liac-arff'` to `'auto'` in 1.4. You can set `parser='auto'` to silence this warning. Therefore, an `ImportError` will be raised from 1.4 if the dataset is dense and pandas is not installed. Note that the pandas parser may return different data types. See the Notes Section in fetch_openml's API doc for details.
  warn(


### Dopasowanie modeli

### Model 1

In [5]:
from sklearn.linear_model import LogisticRegression

In [6]:
model1 = LogisticRegression(max_iter = 1000)
model1.fit(X,y)

/usr/local/lib/python3.10/dist-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(


LogisticRegression(max_iter=1000)

### Model 2

In [7]:
from sklearn.ensemble import RandomForestClassifier

In [8]:
model2 = RandomForestClassifier(max_depth=2, random_state=0)
model2.fit(X,y)

RandomForestClassifier(max_depth=2, random_state=0)

### Model 3

In [9]:
from sklearn.ensemble import GradientBoostingClassifier

In [10]:
model3 = GradientBoostingClassifier(n_estimators=100)
model3.fit(X,y)

GradientBoostingClassifier()

### Analiza globalna

In [11]:
exp1 = dx.Explainer(model1, X, y, label = "Regresja")
exp2 = dx.Explainer(model2, X, y, label = "Las losowy")
exp3 = dx.Explainer(model3, X, y, label = "Gradient Boosting")

Preparation of a new explainer is initiated

  -> data              : 303 rows 13 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.ndarray.
  -> target variable   : 303 values
  -> model_class       : sklearn.linear_model._logistic.LogisticRegression (default)
  -> label             : Regresja
  -> predict function  : <function yhat_proba_default at 0x7f47884a4790> will be used (default)
  -> predict function  : Accepts pandas.DataFrame and numpy.ndarray.
  -> predicted values  : min = 0.00133, mean = 0.544, max = 0.997
  -> model type        : classification will be used (default)
  -> residual function : difference between y and yhat (default)
  -> residuals         : min = -0.957, mean = 0.000151, max = 0.958
  -> model_info        : package sklearn

A new explainer has been created!
Preparation of a new explainer is initiated

  -> data              : 303 rows 13 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a num

In [12]:
mp1 = exp1.model_performance(model_type = "classification")
mp2 = exp2.model_performance(model_type = "classification")
mp3 = exp3.model_performance(model_type = "classification")

Wizualizacja wyników

In [13]:
vi1 = exp1.model_parts()
print(vi1.result)
vi1.plot()

        variable  dropout_loss     label
0            age      0.074682  Regresja
1   _full_model_      0.074704  Regresja
2            fbs      0.075068  Regresja
3           chol      0.078665  Regresja
4        restecg      0.078678  Regresja
5       trestbps      0.083057  Regresja
6          slope      0.085477  Regresja
7          exang      0.086693  Regresja
8           thal      0.094383  Regresja
9        thalach      0.096329  Regresja
10       oldpeak      0.101146  Regresja
11           sex      0.109350  Regresja
12            ca      0.112569  Regresja
13            cp      0.123276  Regresja
14    _baseline_      0.502431  Regresja


In [14]:
vi2 = exp2.model_parts()
print(vi2.result)
vi2.plot()

        variable  dropout_loss       label
0   _full_model_      0.070751  Las losowy
1            fbs      0.070839  Las losowy
2        restecg      0.070883  Las losowy
3       trestbps      0.071124  Las losowy
4           chol      0.071739  Las losowy
5            age      0.072549  Las losowy
6        thalach      0.073022  Las losowy
7          slope      0.075793  Las losowy
8            sex      0.075872  Las losowy
9          exang      0.076173  Las losowy
10       oldpeak      0.082121  Las losowy
11            ca      0.099394  Las losowy
12          thal      0.108961  Las losowy
13            cp      0.109605  Las losowy
14    _baseline_      0.499842  Las losowy


In [15]:
vi3 = exp3.model_parts()
print(vi3.result)
vi3.plot()

        variable  dropout_loss              label
0   _full_model_      0.000659  Gradient Boosting
1            fbs      0.000694  Gradient Boosting
2          exang      0.001357  Gradient Boosting
3        restecg      0.002565  Gradient Boosting
4          slope      0.004023  Gradient Boosting
5       trestbps      0.005753  Gradient Boosting
6        thalach      0.006781  Gradient Boosting
7            sex      0.007106  Gradient Boosting
8           chol      0.010070  Gradient Boosting
9            age      0.011928  Gradient Boosting
10       oldpeak      0.016983  Gradient Boosting
11          thal      0.022240  Gradient Boosting
12            cp      0.024146  Gradient Boosting
13            ca      0.052916  Gradient Boosting
14    _baseline_      0.483285  Gradient Boosting


### Porównanie wybranych modeli

In [16]:
vi1.plot([vi2, vi3])

Dla regresji najbardziej istotne są zmienne cp, ca, sex. W przypadku lasu losowego najważniejsze są zmienne cp, ca, thal. Dla algorytmu gradient boosting najbardziej istotne są zmienne ca, cp, thal, oldpeak.

Na podstawie przeprowadzonej permutacyjnej istotności zmiennych możemy przypuszczać, że globalnie najbardziej istotne są zmienne cp, ca, oraz thal (oznaczają one ból w klatce piersiowej, liczbę głównych naczyń, choroby związane z produkcją hemoglobiny). Potencjalnie kolejnymi zmiennymi, które mają pewien mniejszy wpływ na predykcję, są zmienne oldpeak oraz płeć.  

### Sprawdzenie jakości predykcyjnej

In [26]:
# dziele zbior na czesc treningowa i testowa dla wszystkich zmiennych
# oraz tylko dla wybranych trzech zmiennych istotnych
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
X_new = X.loc[:,['cp', 'ca', 'thal']]
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.25)
X_train_new, X_test_new, y_train_new, y_test_new = train_test_split(X_new, y, test_size=0.25)

Dokładności dla pelnych danych

In [27]:
m_1 = LogisticRegression(max_iter = 1000)
m_1.fit(X_train, y_train)
y_pred_1 = m_1.predict(X_test)
print("Regresja")
print(accuracy_score(y_test, y_pred_1))
m_2 = RandomForestClassifier(max_depth=2, random_state=0)
m_2.fit(X_train, y_train)
y_pred_2 = m_2.predict(X_test)
print("Las losowy")
print(accuracy_score(y_test, y_pred_2))
m_3 = GradientBoostingClassifier(n_estimators=100)
m_3.fit(X_train, y_train)
y_pred_3 = m_3.predict(X_test)
print("Gradient boosting")
print(accuracy_score(y_test, y_pred_3))


Regresja
0.8421052631578947
Las losowy
0.8026315789473685
Gradient boosting
0.7236842105263158


Dokładności w sytuacji ograniczenia się do najbardziej istotnych zmiennych nie ulegają znaczącemu pogorszeniu.

In [28]:
m_1_new = LogisticRegression(max_iter = 1000)
m_1_new.fit(X_train_new, y_train_new)
y_pred_1_new = m_1_new.predict(X_test_new)
print("Regresja")
print(accuracy_score(y_test_new, y_pred_1_new))

m_2_new = RandomForestClassifier(max_depth=2, random_state=0)
m_2_new.fit(X_train_new, y_train_new)
y_pred_2_new = m_2_new.predict(X_test_new)
print("Las losowy")
print(accuracy_score(y_test_new, y_pred_2_new))
m_3_new = GradientBoostingClassifier(n_estimators=100)
m_3_new.fit(X_train_new, y_train_new)
y_pred_3_new = m_3_new.predict(X_test_new)
print("Gradient boosting")
print(accuracy_score(y_test_new, y_pred_3_new))

Regresja
0.7894736842105263
Las losowy
0.8157894736842105
Gradient boosting
0.7894736842105263


Po wybraniu najistotniejszych zmiennych zauważamy, że jakość predykcji modelu wzrasta.

### Profile częściowej zależności

W pierwszym kroku dla wszystkich zmiennych, możemy tutaj przekonać się, że dla zmiennych które zostały uznane wcześniej za mało istotne wykres jest w przybliżeniu stałą funkcją

In [29]:
pdp_num1a = exp1.model_profile(type = 'accumulated', label="Regresja")
pdp_num1b = exp2.model_profile(type = 'accumulated', label="Las losowy")
pdp_num1c = exp3.model_profile(type = 'accumulated', label="Gradient Boosting")
pdp_num1a.plot([pdp_num1b, pdp_num1c])

Calculating accumulated dependency: 100%|██████████| 13/13 [00:01<00:00,  7.19it/s]


Teraz wykresy tylko dla wybranych istotnych zmiennych

In [30]:
exp1_new = dx.Explainer(m_1_new, X_new, y, label = "Regresja")
exp2_new = dx.Explainer(m_2_new, X_new, y, label = "Las losowy")
exp3_new = dx.Explainer(m_3_new, X_new, y, label = "Gradient Boosting")
tmp1 = exp1_new.model_profile(type = 'partial', label="Regresja")
tmp2 = exp2_new.model_profile(type = 'partial', label="Las losowy")
tmp3 = exp3_new.model_profile(type = 'partial', label="Gradient Boosting")
tmp1.plot([tmp2, tmp3])

Preparation of a new explainer is initiated

  -> data              : 303 rows 3 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.ndarray.
  -> target variable   : 303 values
  -> model_class       : sklearn.linear_model._logistic.LogisticRegression (default)
  -> label             : Regresja
  -> predict function  : <function yhat_proba_default at 0x7f47884a4790> will be used (default)
  -> predict function  : Accepts pandas.DataFrame and numpy.ndarray.
  -> predicted values  : min = 0.0105, mean = 0.543, max = 0.977
  -> model type        : classification will be used (default)
  -> residual function : difference between y and yhat (default)
  -> residuals         : min = -0.949, mean = 0.00162, max = 0.976
  -> model_info        : package sklearn

A new explainer has been created!
Preparation of a new explainer is initiated

  -> data              : 303 rows 3 cols
  -> target variable   : Parameter 'y' was a pandas.Series. Converted to a numpy.n

Calculating ceteris paribus: 100%|██████████| 3/3 [00:00<00:00, 32.56it/s]


Z powyższych wykresów możemy zauważyć, że zmiana wartości wybranych trzech zmiennych powoduje zmianę predykcji modelu (wykresy nie są linią prostą na całym zakresie). Jest to potwierdzeniem, że wybrane zmienne mają istotny wpływ na model. Najbardziej czuły na różnice w wartościach wybranych zmiennych jest model regresji liniowej, potwierdzeniem na to są szczególnie dwa pierwsze wykresy.

### Analiza lokalna

In [48]:
# Znajduje obserwacje ktora jest przewidywana poprawnie przez wszystkie trzy modele
pos_1 = np.where((y_test == y_pred_1) )[0]
pos_2 = np.where((y_test == y_pred_2) )[0]
pos_3 = np.where((y_test == y_pred_3) )[0]
pos = np.intersect1d(np.intersect1d(pos_1, pos_2), pos_3)
# nastepnie sposrod wszystkich tak wybranych obserwacji wybieram dowolna z nich
pos_index = pos[6]
print(y_test.iloc[pos_index])

1


In [36]:
# Znajduje obserwacje ktora jest niepoprawnie przewidywana przez wszystkie trzy modele
err_1 = np.where((y_test != y_pred_1) )[0]
err_2 = np.where((y_test != y_pred_2) )[0]
err_3 = np.where((y_test != y_pred_3) )[0]
err = np.intersect1d(np.intersect1d(err_1, err_2), err_3)
# nastepnie sposrod wszystkich tak wybranych obserwacji wybieram dowolna z nich
neg_index = err[0]

In [49]:
# dla pierwszej wybranej obserwacji obliczam dekompozycję predykcji modelu
bd_1 = exp1.predict_parts(X_train.iloc[pos_index,:], type = "break_down")
bd_2 = exp2.predict_parts(X_train.iloc[pos_index,:], type = "break_down")
bd_3 = exp3.predict_parts(X_train.iloc[pos_index,:], type = "break_down")
bd_1.plot([bd_2, bd_3])

Wyniki pokazują, jak dane wartości odpowiednich zmiennych wpływają na końcową predykcję. W przypadku modelu regresji zmienną którą w największy sposób obniżyła prawdopodobieństwo trafienia do klasy 1 była zmienna cp (możemy odczytać to z tabeli poniżej), natomiast zmienne sex oraz ca miały największy udział we wzroście prawdopodobieństwa wpadnięcia do klasy nr 1.

W modelu las losowy i gradient boostingu zmienna thal miała największy wkład we wzrost prawdopodobieństwa przypisania do klasy 1, w modelu las losowy zmienne restecg, chol, cp odpowiadały za zmniejszenie prawdopodobieństwa przypisania do klasy nr 1, w gradient boosting odpowiadały za to zmienne fbs, cp.

Dokładny wpływ wartości poszczególnej zmiennej na predykcję możemy odczytać z tabeli.

In [50]:
bd_1 # dla modelu regresji logistycznej

In [51]:
bd_2 # dla las losowy

In [52]:
bd_3 # dla gradient boosting

In [34]:
# teraz dla drugiej wybranej zmiennej
bd_1a = exp1.predict_parts(X_train.iloc[neg_index,:], type = "break_down")
bd_2a = exp2.predict_parts(X_train.iloc[neg_index,:], type = "break_down")
bd_3a = exp3.predict_parts(X_train.iloc[neg_index,:], type = "break_down")
bd_1a.plot([bd_2a, bd_3a])

Widzimy, że w przeciwieństwie do pierwszej wybranej obserwacji, dla drugiej wybranej obserwacji zmienna cp ma największą rolę w zwiększaniu prawdopodobieństwa przypisania do klasy nr 1. Z tabel poniżej możemy odczytać, które zmienne miały największy wpływ na spadek prawdopodobieństwa.

In [ ]:
bd_1a # dla regresji

In [ ]:
bd_2a # las losowy

In [ ]:
bd_3a # gradient boosting

### Wykres Ceteris Paribus

In [53]:
cp_1 = exp1.predict_profile(X_train.iloc[pos_index,:])
cp_2 = exp2.predict_profile(X_train.iloc[pos_index,:])
cp_3 = exp3.predict_profile(X_train.iloc[pos_index,:])
cp_1.plot([cp_2, cp_3])

Calculating ceteris paribus: 100%|██████████| 13/13 [00:00<00:00, 141.84it/s]


Wykres ten wskazuje możliwe scenariusze przewidywań modelu, które zakładają zmiany jednej cechy przy zachowaniu wszystkich innych cech na stałym poziomie. Możemy odczytać, że na predykcje ma wpływ zmiana zmiennych ca, cp oraz thal. Możemy także zauważyć, że zmienne sex, thalach, trestbps, oldpeak mają zauważalnie większy wpływ na predykcję w modelu regresji niż w pozostałych dwóch modelach. Uzyskane wyniki potwierdzają rezultaty uzyskane podczas analizy globalnej.

In [54]:
cp_1 = exp1.predict_profile(X_train.iloc[neg_index,:])
cp_2 = exp2.predict_profile(X_train.iloc[neg_index,:])
cp_3 = exp3.predict_profile(X_train.iloc[neg_index,:])
cp_1.plot([cp_2, cp_3])

Calculating ceteris paribus: 100%|██████████| 13/13 [00:00<00:00, 251.65it/s]


Dla drugiej wybranej obserwacji możemy sformułować podobne wnioski.

### Podsumowanie

Dzięki wyjaśnialnemu uczeniu maszynowemu możemy w ciekawy i przyjemny sposób uzyskać i zwizualizować interpretację trenowanego modelu,
co może być bardzo przydatne w praktycznych zastosowaniach.